In [1]:
%load_ext autoreload
%autoreload 2
%matplotlib inline

In [2]:
from fastai.imports import *
from fastai.structured import *
from pandas_summary import DataFrameSummary
from sklearn.ensemble import RandomForestRegressor, RandomForestClassifier
from IPython.display import display
from sklearn import metrics

In [5]:
!dir "data/bluebook-for-bulldozers/"

 Volume in drive D is LENOVO
 Volume Serial Number is 7C94-5EA5

 Directory of D:\MyPortfolio\Blue_Book_For_Bulldozers\data\bluebook-for-bulldozers

09-Aug-19  01:15 AM    <DIR>          .
09-Aug-19  01:15 AM    <DIR>          ..
28-Apr-18  12:21 PM            11,063 Data Dictionary.xlsx
28-Apr-18  12:21 PM        51,498,702 Machine_Appendix.csv
28-Apr-18  12:21 PM           196,760 median_benchmark.csv
28-Apr-18  12:21 PM           211,941 random_forest_benchmark_test.csv
28-Apr-18  12:21 PM         3,560,907 Test.csv
24-Jan-13  04:08 PM       116,403,970 Train.csv
28-Apr-18  12:21 PM       119,791,159 TrainAndValid.csv
28-Apr-18  12:21 PM         3,318,969 Valid.csv
28-Apr-18  12:21 PM           323,524 ValidSolution.csv
               9 File(s)    295,316,995 bytes
               2 Dir(s)  510,516,473,856 bytes free


In [6]:
df_raw = pd.read_csv("data/bluebook-for-bulldozers/TrainAndValid.csv", low_memory = False, parse_dates = ["saledate"])

In [7]:
df_raw

SalesID  SalePrice  MachineID  ModelID  datasource  auctioneerID  \
0       1139246    66000.0     999089     3157         121           3.0   
1       1139248    57000.0     117657       77         121           3.0   
2       1139249    10000.0     434808     7009         121           3.0   
3       1139251    38500.0    1026470      332         121           3.0   
4       1139253    11000.0    1057373    17311         121           3.0   
5       1139255    26500.0    1001274     4605         121           3.0   
6       1139256    21000.0     772701     1937         121           3.0   
7       1139261    27000.0     902002     3539         121           3.0   
8       1139272    21500.0    1036251    36003         121           3.0   
9       1139275    65000.0    1016474     3883         121           3.0   
10      1139278    24000.0    1024998     4605         121           3.0   
11      1139282    22500.0     319906     5255         121           3.0   
12      1139283    36000.0    1052214     2232         121           3.0   
13      1139284    30500.0    1068082     3542         121           3.0   
14      1139290    28000.0    1058450     5162         121           3.0   
15      1139291    19000.0    1004810     4604         121           3.0   
16      1139292    13500.0    1026973     9510         121           3.0   
17      1139299     9500.0    1002713    21442         121           3.0   
18      1139301    12500.0     125790     7040         121           3.0   
19      1139304    11500.0    1011914     3177         121           3.0   
20      1139311    41000.0    1014135     8867         121           3.0   
21      1139333    34500.0     999192     3350         121           3.0   
22      1139344    26000.0    1044500     7040         121           3.0   
23      1139346    73000.0     821452       85         121           3.0   
24      1139348    33000.0     294562     3542         121           3.0   
25      1139351    12500.0     833838     7009         121           3.0   
26      1139354    15500.0     565440     7040         121           3.0   
27      1139356    53000.0    1004127    25458         121           3.0   
28      1139357    46000.0      44800    19167         121           3.0   
29      1139358    89000.0    1018076     1333         121           3.0   
...         ...        ...        ...      ...         ...           ...   
412668  6333224    27500.0    1872450    21450         149           2.0   
412669  6333225    23000.0    1835816    21450         149           2.0   
412670  6333228    17500.0    1876109    21449         149           2.0   
412671  6333229    10500.0    1686621    21434         149           4.0   
412672  6333236    11500.0    1890101    21434         149           1.0   
412673  6333244     9000.0    1816767    21434         149           2.0   
412674  6333248    12000.0    1796000    21434         149           2.0   
412675  6333265    12000.0    1867553    21437         149           2.0   
412676  6333266    12500.0    1882568    21437         149           2.0   
412677  6333267    14000.0    1841621    21437         149           2.0   
412678  6333268    14500.0    1841583    21437         149           2.0   
412679  6333269    13000.0    1912837    21437         149           2.0   
412680  6333271    11000.0    1833970    21437         149           2.0   
412681  6333286    13000.0    1797899    21437         149           2.0   
412682  6333288    12500.0    1870701    21437         149          99.0   
412683  6333294    10000.0    1861122    21437         149           1.0   
412684  6333295    10000.0    1795071    21437         149           1.0   
412685  6333298    10000.0    1799329    21437         149           1.0   
412686  6333299    10000.0    1881324    21437         149           1.0   
412687  6333303    10500.0    1927462    21437         149           1.0   
412688  6333305    11500.0    1800259    21437         1

In [8]:
df_appendix = pd.read_csv("data/bluebook-for-bulldozers/Machine_Appendix.csv", low_memory = False)

In [9]:
def display_all(df):
    with pd.option_context("display.max_rows", 1000, "display.max_columns", 1000):
        display(df)

In [11]:
display_all(df_appendix)

MachineID  ModelID   fiModelDesc fiBaseModel fiSecondaryDesc  \
0             113     1355          350L         350             NaN   
1             434     3538          416C         416               C   
2             534     3538          416C         416               C   
3             718     3538          416C         416               C   
4            1753     1580        D5GLGP          D5               G   
5            2055     3538          416C         416               C   
6            2473     1580        D5GLGP          D5               G   
7            2656     3538          416C         416               C   
8            3088     1580        D5GLGP          D5               G   
9            3389     3538          416C         416               C   
10           3790     3538          416C         416               C   
11           3991     4113           D5C          D5               C   
12           4495     1564        D4HLGP          D4               H   
13           4709     1625        D6NLGP          D6               N   
14           4710     1580        D5GLGP          D5               G   
15           5212     1580        D5GLGP          D5               G   
16           5345     3538          416C         416               C   
17          27959     1580        D5GLGP          D5               G   
18          28675     3538          416C         416               C   
19          28976     2759         D5HII          D5               H   
20          28996    13832         D5GXL          D5               G   
21          29111     1623        D6MLGP          D6               M   
22          29595     3538          416C         416               C   
23          31015     1625        D6NLGP          D6               N   
24          31316     3879          980G         980               G   
25          31970     3538          416C         416               C   
26          32889     3538          416C         416               C   
27          33073     2752        D4CIII          D4               C   
28          33488     3538          416C         416               C   
29           8272     3538          416C         416               C   
30           8303     1580        D5GLGP          D5               G   
31           8874     1605        D6DLGP          D6               D   
32           8889     1598        D5NLGP          D5               N   
33           9522     3538          416C         416               C   
34          10024     3538          416C         416               C   
35          10044    13398         305CR         305             NaN   
36           8694     1078         304CR         304             NaN   
37           9187     1339         345CL         345               C   
38           9712     3538          416C         416               C   
39          10039     1598        D5NLGP          D5               N   
40          10128     1598        D5NLGP          D5               N   
41          10523     3538          416C         416               C   
42          11552     1580        D5GLGP          D5               G   
43          11759     1355          350L         350             NaN   
44          12184     3538          416C         416               C   
45          12284    23242       365BLII         365              BL   
46          12554     1623        D6MLGP          D6               M   
47          34287     1623        D6MLGP          D6               M   
48          34389     3538          416C         416               C   
49          34503     2759         D5HII          D5               H   
50          34914     3861          970F         970               F   
51          35298     3552          430D         430               D   
52          36870     3547          426C         426               C   
53          37338     4113           D5C          D5               C   
54          38790     3538          416C        

In [13]:
df_raw.shape, df_appendix.shape

((412698, 53), (358593, 16))

In [18]:
d = pd.merge(df_raw, df_appendix, on="MachineID", suffixes=("", "_y"))

In [19]:
display_all(d)

SalesID  SalePrice  MachineID  ModelID  datasource  auctioneerID  \
0       1139246    66000.0     999089     3157         121           3.0   
1       1139248    57000.0     117657       77         121           3.0   
2       1139249    10000.0     434808     7009         121           3.0   
3       1398858    12000.0     434808     7009         132           2.0   
4       1398859    12500.0     434808     7009         132           2.0   
5       1139251    38500.0    1026470      332         121           3.0   
6       1139253    11000.0    1057373    17311         121           3.0   
7       1139255    26500.0    1001274     4605         121           3.0   
8       1139256    21000.0     772701     1937         121           3.0   
9       1175843    29500.0     772701     8323         121           3.0   
10      1139261    27000.0     902002     3539         121           3.0   
11      1139272    21500.0    1036251    36003         121           3.0   
12      1139275    65000.0    1016474     3883         121           3.0   
13      1139278    24000.0    1024998     4605         121           3.0   
14      1139282    22500.0     319906     5255         121           3.0   
15      1185515     8000.0     319906      328         121           3.0   
16      1139283    36000.0    1052214     2232         121           3.0   
17      1770625    50000.0    1052214     2232         132           3.0   
18      4359500    45000.0    1052214    23623         172           1.0   
19      1139284    30500.0    1068082     3542         121           3.0   
20      1139290    28000.0    1058450     5162         121           3.0   
21      1139291    19000.0    1004810     4604         121           3.0   
22      1139292    13500.0    1026973     9510         121           3.0   
23      1139299     9500.0    1002713    21442         121           3.0   
24      1139301    12500.0     125790     7040         121           3.0   
25      1139304    11500.0    1011914     3177         121           3.0   
26      1139311    41000.0    1014135     8867         121           3.0   
27      1139333    34500.0     999192     3350         121           3.0   
28      1139344    26000.0    1044500     7040         121           3.0   
29      1139346    73000.0     821452       85         121           3.0   
30      1139348    33000.0     294562     3542         121           3.0   
31      1139351    12500.0     833838     7009         121           3.0   
32      1139354    15500.0     565440     7040         121           3.0   
33      1139356    53000.0    1004127    25458         121           3.0   
34      1139357    46000.0      44800    19167         121           3.0   
35      1139358    89000.0    1018076     1333         121           3.0   
36      1139363    51000.0     871201     1263         121           3.0   
37      1139365    14000.0     973717     9566         121           3.0   
38      1139367    31500.0    1036100     9109         121           3.0   
39      1139369    14000.0    1050658     1918         121           3.0   
40      1139379    18500.0      70214    13395         121           3.0   
41      1139382    10000.0    1068548      112         121           3.0   
42      1139390     8250.0    1011114     7110         121           3.0   
43      1139398    20500.0     138847     7043         121           3.0   
44      1139401     9500.0    1011478    18604         121           3.0   
45      1139409    51000.0     999090     3362         121           3.0   
46      1139412    39000.0     108090     1088         121           3.0   
47      1139413    58000.0    1045512     5853         121           3.0   
48      1139415    15500.0    1066239    17188         121           3.0   
49      1139418     7750.0    1026462     6270         121           3.0   
50      1139421    32000.0    1048704     2797         121           3.0   
51      1139423    11500.0     999442     3217         1

In [33]:
df_raw = d.drop(columns=list(d.filter(regex="_y$").columns))

In [36]:
df_raw.shape

(412698, 59)

In [38]:
df_raw.SalePrice = np.log(df_raw.SalePrice)

In [39]:
add_datepart(df_raw, 'saledate')

In [41]:
df_raw.columns

Index(['SalesID', 'SalePrice', 'MachineID', 'ModelID', 'datasource',
       'auctioneerID', 'YearMade', 'MachineHoursCurrentMeter', 'UsageBand',
       'fiModelDesc', 'fiBaseModel', 'fiSecondaryDesc', 'fiModelSeries',
       'fiModelDescriptor', 'ProductSize', 'fiProductClassDesc', 'state',
       'ProductGroup', 'ProductGroupDesc', 'Drive_System', 'Enclosure',
       'Forks', 'Pad_Type', 'Ride_Control', 'Stick', 'Transmission',
       'Turbocharged', 'Blade_Extension', 'Blade_Width', 'Enclosure_Type',
       'Engine_Horsepower', 'Hydraulics', 'Pushblock', 'Ripper', 'Scarifier',
       'Tip_Control', 'Tire_Size', 'Coupler', 'Coupler_System',
       'Grouser_Tracks', 'Hydraulics_Flow', 'Track_Type',
       'Undercarriage_Pad_Width', 'Stick_Length', 'Thumb', 'Pattern_Changer',
       'Grouser_Type', 'Backhoe_Mounting', 'Blade_Type', 'Travel_Controls',
       'Differential_Type', 'Steering_Controls', 'MfgYear', 'fiManufacturerID',
       'fiManufacturerDesc', 'PrimarySizeBasis', 'PrimaryL

In [43]:
display_all(df_raw.head())

SalesID  SalePrice  MachineID  ModelID  datasource  auctioneerID  YearMade  \
0  1139246  11.097410     999089     3157         121           3.0      2004   
1  1139248  10.950807     117657       77         121           3.0      1996   
2  1139249   9.210340     434808     7009         121           3.0      2001   
3  1398858   9.392662     434808     7009         132           2.0      2001   
4  1398859   9.433484     434808     7009         132           2.0      2001   

   MachineHoursCurrentMeter UsageBand fiModelDesc fiBaseModel fiSecondaryDesc  \
0                      68.0       Low        521D         521               D   
1                    4640.0       Low      950FII         950               F   
2                    2838.0      High         226         226             NaN   
3                       NaN       NaN         226         226             NaN   
4                       NaN       NaN         226         226             NaN   

  fiModelSeries fiModelDescriptor ProductSize  \
0           NaN               NaN         NaN   
1            II               NaN      Medium   
2           NaN               NaN         NaN   
3           NaN               NaN         NaN   
4           NaN               NaN         NaN   

                                  fiProductClassDesc           state  \
0           Wheel Loader - 110.0 to 120.0 Horsepower         Alabama   
1           Wheel Loader - 150.0 to 175.0 Horsepower  North Carolina   
2  Skid Steer Loader - 1351.0 to 1601.0 Lb Operat...        New York   
3  Skid Steer Loader - 1351.0 to 1601.0 Lb Operat...        Kentucky   
4  Skid Steer Loader - 1351.0 to 1601.0 Lb Operat...           Texas   

  ProductGroup    ProductGroupDesc Drive_System   Enclosure  \
0           WL        Wheel Loader          NaN  EROPS w AC   
1           WL        Wheel Loader          NaN  EROPS w AC   
2          SSL  Skid Steer Loaders          NaN       OROPS   
3          SSL  Skid Steer Loaders          NaN       OROPS   
4          SSL  Skid Steer Loaders          NaN       OROPS   

                 Forks Pad_Type         Ride_Control Stick Transmission  \
0  None or Unspecified      NaN  None or Unspecified   NaN          NaN   
1  None or Unspecified      NaN  None or Unspecified   NaN          NaN   
2  None or Unspecified      NaN                  NaN   NaN          NaN   
3  None or Unspecified      NaN                  NaN   NaN          NaN   
4  None or Unspecified      NaN                  NaN   NaN          NaN   

  Turbocharged Blade_Extension Blade_Width Enclosure_Type Engine_Horsepower  \
0          NaN             NaN         NaN            NaN               NaN   
1          NaN             NaN         NaN            NaN               NaN   
2          NaN             NaN         NaN            NaN               NaN   
3          NaN             NaN         NaN            NaN               NaN   
4          NaN             NaN         NaN            NaN               NaN   

  Hydraulics Pushblock Ripper Scarifier Tip_Control            Tire_Size  \
0    2 Valve       NaN    NaN       NaN         NaN  None or Unspecified   
1    2 Valve       NaN    NaN       NaN         NaN                 23.5   
2  Auxiliary       NaN    NaN       NaN         NaN                  NaN   
3  Auxiliary       NaN    NaN       NaN         NaN                  NaN   
4  Auxiliary       NaN    NaN       NaN         NaN                  NaN   

               Coupler       Coupler_System       Grouser_Tracks  \
0  None or Unspecified                  NaN                  NaN   
1  None or Unspecified                  NaN                  NaN   
2  None or Unspecified  None or Unspecified  None or Unspecified   
3  None or Unspecified  None or Unspecified  None or Unspecified   
4  None or Unspecified  None or Unspecified  None or Unspecified   

  Hydraulics_Flow Track_Type Undercarriage_Pad_Width Stick_Length Thumb  \
0             NaN        NaN                     NaN   

In [44]:
train_cats(df_raw)

In [48]:
df_raw.UsageBand.cat.categories

Index(['High', 'Low', 'Medium'], dtype='object')

In [49]:
df_raw.UsageBand.cat.set_categories(['High', 'Medium', 'Low'], ordered=True, inplace = True)

In [50]:
df_raw.UsageBand.cat.categories

Index(['High', 'Medium', 'Low'], dtype='object')

In [53]:
display_all(df_raw.isnull())

SalesID  SalePrice  MachineID  ModelID  datasource  auctioneerID  \
0         False      False      False    False       False         False   
1         False      False      False    False       False         False   
2         False      False      False    False       False         False   
3         False      False      False    False       False         False   
4         False      False      False    False       False         False   
5         False      False      False    False       False         False   
6         False      False      False    False       False         False   
7         False      False      False    False       False         False   
8         False      False      False    False       False         False   
9         False      False      False    False       False         False   
10        False      False      False    False       False         False   
11        False      False      False    False       False         False   
12        False      False      False    False       False         False   
13        False      False      False    False       False         False   
14        False      False      False    False       False         False   
15        False      False      False    False       False         False   
16        False      False      False    False       False         False   
17        False      False      False    False       False         False   
18        False      False      False    False       False         False   
19        False      False      False    False       False         False   
20        False      False      False    False       False         False   
21        False      False      False    False       False         False   
22        False      False      False    False       False         False   
23        False      False      False    False       False         False   
24        False      False      False    False       False         False   
25        False      False      False    False       False         False   
26        False      False      False    False       False         False   
27        False      False      False    False       False         False   
28        False      False      False    False       False         False   
29        False      False      False    False       False         False   
30        False      False      False    False       False         False   
31        False      False      False    False       False         False   
32        False      False      False    False       False         False   
33        False      False      False    False       False         False   
34        False      False      False    False       False         False   
35        False      False      False    False       False         False   
36        False      False      False    False       False         False   
37        False      False      False    False       False         False   
38        False      False      False    False       False         False   
39        False      False      False    False       False         False   
40        False      False      False    False       False         False   
41        False      False      False    False       False         False   
42        False      False      False    False       False         False   
43        False      False      False    False       False         False   
44        False      False      False    False       False         False   
45        False      False      False    False       False         False   
46        False      False      False    False       False         False   
47        False      False      False    False       False         False   
48        False      False      False    False       False         False   
49        False      False      False    False       False         False   
50        False      False      False    False       False         False   
51        False      False      False    False       Fal